# **Reproducing M1+M2 results (Table 3)**

<a target="_blank" href="https://colab.research.google.com/github/blackswan-advitamaeternam/HVAE/blob/raph/paper_experiments/Table3_exp.ipynb"> <img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/> </a>

## **Colab setup**

In [1]:
from google.colab import drive
drive.mount('/content/drive')
# to avoid having the data on your drive
%cd /content

Mounted at /content/drive
/content


In [2]:
!git clone https://github.com/blackswan-advitamaeternam/HVAE.git
%cd HVAE
!git checkout raph
!pip install -r requirements.txt

Cloning into 'HVAE'...
remote: Enumerating objects: 354, done.
remote: Counting objects: 100% (37/37), done.
remote: Compressing objects: 100% (34/34), done.
remote: Total 354 (delta 6), reused 8 (delta 3), pack-reused 317 (from 1)
Receiving objects: 100% (354/354), 276.30 KiB | 641.00 KiB/s, done.
Resolving deltas: 100% (228/228), done.
/content/HVAE
Branch 'raph' set up to track remote branch 'raph' from 'origin'.
Switched to a new branch 'raph'
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 77.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 174.2/174.2 kB 18.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.6/58.6 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 284.1/284.1 kB 21.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.2/9.2 MB 102.3 MB/s eta 0:00:00


To allow automatic reloading

In [3]:
!pip install --upgrade ipython

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 621.4/621.4 kB 45.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 73.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.4/85.4 kB 7.4 MB/s eta 0:00:00
  Attempting uninstall: traitlets
    Found existing installation: traitlets 5.7.1
    Uninstalling traitlets-5.7.1:
      Successfully uninstalled traitlets-5.7.1
  Attempting uninstall: ipython
    Found existing installation: ipython 7.34.0
    Uninstalling ipython-7.34.0:
      Successfully uninstalled ipython-7.34.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires ipython==7.34.0, but you have ipython 9.8.0 which is incompatible.


In [4]:
import sys
try:
    import imp
except ImportError:
    import types
    sys.modules['imp'] = types.ModuleType('imp')

In [5]:
%load_ext autoreload
%autoreload 2

## **Imports**

In [6]:
import sys, os
# To ensure the custom package is found
path_to_repo = "/content/HVAE"
if path_to_repo not in sys.path:
    sys.path.append(path_to_repo)

In [7]:
import numpy as np
import pandas as pd
import torch
from tqdm.auto import tqdm
from sklearn.metrics import accuracy_score

from svae.vae import M1_M2, predict_classes_loader, cluster_acc
from svae.training import training_M1M2
from svae.utils import ShuffledLoader

from paper_experiments.load_MNIST import make_splits_loaders_MNIST

/content/HVAE/paper_experiments/load_MNIST.py
/content/HVAE/paper_experiments


Setting device

In [8]:
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [9]:
# make splits
NUM_WORKERS = int(0.8*os.cpu_count())
FRAC = 0.1
TRAIN_FRAC = int(50000 * FRAC)
VAL_FRAC = int(10000 * FRAC)
TEST_FRAC = None # potentially still test on all test samples
print(f"Using {NUM_WORKERS} workers.")
train_loader, val_loader, test_loader = make_splits_loaders_MNIST(train_size=TRAIN_FRAC, val_size=VAL_FRAC, test_size=TEST_FRAC,
                                                                batch_size=100,
                                                                test_batch_size=100,
                                                                num_workers=NUM_WORKERS,
                                                                prefetch_factor=2,
                                                                force=True,
                                                                persistent_workers=True,
                                                                pin_memory=True)

Using 1 workers.

Making splits..


Dl Completed...: 0 url [00:00, ? url/s]

Dl Size...: 0 MiB [00:00, ? MiB/s]

Extraction completed...: 0 file [00:00, ? file/s]

Generating splits...:   0%|          | 0/2 [00:00<?, ? splits/s]

Generating train examples...: 0 examples [00:00, ? examples/s]

Shuffling /root/tensorflow_datasets/mnist/incomplete.QR60UG_3.0.1/mnist-train.tfrecord*...:   0%|          | 0…

Generating test examples...: 0 examples [00:00, ? examples/s]

Shuffling /root/tensorflow_datasets/mnist/incomplete.QR60UG_3.0.1/mnist-test.tfrecord*...:   0%|          | 0/…

Dataset mnist downloaded and prepared to /root/tensorflow_datasets/mnist/3.0.1. Subsequent calls will reuse this data.
600
torch.Size([60000, 784])
100
torch.Size([10000, 784])
Train 5000
Val 1000
Test 10000


In [ ]:
# Manifesting to memory of the device (we can afford it on colab ?)
train_batches = [[el.to(DEVICE) for el in batch] for batch in train_loader]

# we pick a random batch to be used fully labeled (as batch_size = 100, N=100 by the authors is one batch)
labeled_idx = int(np.random.randint(0, len(train_batches), 1)[0])
labeled_train_batches = [train_batches[labeled_idx]] # Prepare labeled loader
unlabeled_train_batches = [batch for i, batch in enumerate(train_batches) if i != labeled_idx] # unlabeled

val_batches   = [[el.to(DEVICE) for el in batch] for batch in val_loader]
test_batches  = [[el.to(DEVICE) for el in batch] for batch in test_loader]

# Wrap for shuffling behavior
unlabeled_train_loader = ShuffledLoader(
    unlabeled_train_batches,
    shuffle_batches=True,
    shuffle_within_batch=True,
    device_for_randperm=DEVICE)

labeled_train_loader = labeled_train_batches

val_loader = val_batches
test_loader = test_batches

We will only test on $N = 100$

## **Configuration**

In [26]:
base_path = "/content/drive/MyDrive/HVAE/Table3/"
os.makedirs(base_path, exist_ok=True)

In [27]:
EPOCHS = 500
INPUT_DIM = 784
HIDDEN_DIM = 500
N_CLUSTERS = 10
LATENT_MODE = 'sample'
WARMUP = 100
PATIENCE = 50
ONE_LAYER = True
LR = 1e-3

N_RUNS = 5

In [ ]:
def run_and_test(mode1, mode2, latent1, latent2, test_dataloader):
    addon = "SVAE" if mode1 == "svae" else "NVAE"
    addon = addon + " + SVAE" if mode1 == "svae" else " + NVAE"
    addon = f"[{addon}]"

    print(f"\n{addon} Instantiating SVAE and optimizer..")
    model = M1_M2(mode1,
                mode2,
                INPUT_DIM,
                HIDDEN_DIM,
                latent1,
                latent2,
                N_CLUSTERS,
                ONE_LAYER,
                )

    # To device
    model.to(DEVICE)

    optimizer = torch.optim.Adam(model.parameters(), lr=LR)

    print(f"{addon} Started training..")
    model, losses, all_parts = training_M1M2(unlabeled_train_loader,
                                    labeled_train_loader,
                                    val_loader,
                                    model,
                                    optimizer,
                                    epochs=EPOCHS,
                                    beta_kl=1,
                                    warmup=WARMUP,
                                    alpha=1.0,
                                    patience=PATIENCE,
                                    show_loss_every=1)

    print(f"\n{addon} Predicting classes..")
    Y, Y_hat = predict_classes_loader(model, test_dataloader, LATENT_MODE)

    test_acc = cluster_acc(Y, Y_hat)
    print(f"{addon} Test accuracy: {test_acc*100:.2f}")
    return test_acc

In [32]:
def launch_experiment(mode1, mode2, test_dataloader):
    results_df = {"Latent M1":[], "Latent M2":[], "Model":[], "Accuracy":[], "Std":[], "N_test":[]}
    for latent1 in tqdm([5,10,50], desc="Exploring latent1.."):
        for latent2 in tqdm([5, 10, 50], desc="Exploring latent2.."):
            accuracy_list = []
            for i in tqdm(list(range(N_RUNS)), desc="Repeated runs.."):
                print(f"\nSTARTING RUN n°{i+1}")
                accuracy_list.append(run_and_test(mode1, mode2, latent1, latent2, test_dataloader))
            avg_acc = np.nanmean(accuracy_list)
            std_acc = np.nanstd(accuracy_list)

            results_df["Latent M1"].append(latent1)
            results_df["Latent M2"].append(latent2)
            results_df["Model"].append(mode1 + " + " + mode2)
            results_df["Accuracy"].append(avg_acc)
            results_df["Std"].append(std_acc)
            results_df["N_test"].append(100)
    return pd.DataFrame(results_df)

## **SVAE + SVAE**

In [33]:
results_df_svae_svae = launch_experiment("svae", "svae", test_loader)

Exploring latent1..:   0%|          | 0/3 [00:00<?, ?it/s]

Exploring latent2..:   0%|          | 0/3 [00:00<?, ?it/s]

Repeated runs..:   0%|          | 0/5 [00:00<?, ?it/s]


STARTING RUN n°1

[SVAE + SVAE] Instantiating SVAE and optimizer..
[SVAE + SVAE] Started training..

Moving Categorical Dist to cuda:0


Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

...

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 219.2822 (217.6654 + 1.6168) | train = 372.8448 (370.8719 + 1.9729)
epoch 2: val = 205.5990 (204.0783 + 1.5207) | train = 211.5066 (209.9527 + 1.5539)
epoch 3: val = 197.7838 (196.4283 + 1.3555) | train = 202.1534 (200.7180 + 1.4354)
epoch 4: val = 192.7987 (191.6290 + 1.1696) | train = 195.3405 (194.0977 + 1.2428)
epoch 5: val = 175.7558 (174.8323 + 0.9235) | train = 186.0764 (185.0060 + 1.0704)
epoch 6: val = 158.5137 (157.8507 + 0.6630) | train = 167.2360 (166.4721 + 0.7639)
epoch 7: val = 148.8019 (148.2947 + 0.5072) | train = 153.4702 (152.9253 + 0.5449)
epoch 8: val = 144.5368 (144.1503 + 0.3865) | train = 146.9658 (146.5527 + 0.4131)
epoch 9: val = 140.1244 (139.8107 + 0.3137) | train = 142.6885 (142.3754 + 0.3130)
epoch 10: val = 135.5978 (135.3684 + 0.2295) | train = 137.8349 (137.5953 + 0.2396)
epoch 11: val = 131.9905 (131.8184 + 0.1721) | train = 133.3674 (133.1933 + 0.1741)
e

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 221.1573 (219.5025 + 1.6548) | train = 381.1884 (379.1745 + 2.0139)
epoch 2: val = 205.4215 (203.9026 + 1.5189) | train = 212.0566 (210.4848 + 1.5718)
epoch 3: val = 197.1973 (195.8373 + 1.3600) | train = 201.6039 (200.1667 + 1.4372)
epoch 4: val = 190.6898 (189.5481 + 1.1417) | train = 194.7364 (193.4816 + 1.2548)
epoch 5: val = 171.2249 (170.3561 + 0.8688) | train = 181.5540 (180.5651 + 0.9889)
epoch 6: val = 156.6344 (156.0027 + 0.6317) | train = 164.1511 (163.4314 + 0.7197)
epoch 7: val = 148.4115 (147.9294 + 0.4821) | train = 152.4835 (151.9638 + 0.5197)
epoch 8: val = 143.6974 (143.3246 + 0.3727) | train = 146.3083 (145.9140 + 0.3943)
epoch 9: val = 139.0883 (138.7783 + 0.3100) | train = 141.5484 (141.2313 + 0.3171)
epoch 10: val = 133.9185 (133.6821 + 0.2365) | train = 136.1647 (135.9218 + 0.2429)
epoch 11: val = 130.3563 (130.1865 + 0.1698) | train = 132.2824 (132.1034 + 0.1790)
e

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 219.0032 (217.3896 + 1.6136) | train = 371.6849 (369.7168 + 1.9680)
epoch 2: val = 205.9912 (204.4571 + 1.5341) | train = 212.0183 (210.4668 + 1.5516)
epoch 3: val = 197.7910 (196.4121 + 1.3789) | train = 202.5851 (201.1309 + 1.4542)
epoch 4: val = 189.4929 (188.3096 + 1.1832) | train = 194.7002 (193.4416 + 1.2586)
epoch 5: val = 168.8886 (168.0094 + 0.8792) | train = 179.6244 (178.5959 + 1.0285)
epoch 6: val = 155.7666 (155.1455 + 0.6211) | train = 161.7586 (161.0367 + 0.7219)
epoch 7: val = 147.6856 (147.2010 + 0.4846) | train = 151.6815 (151.1644 + 0.5171)
epoch 8: val = 142.5526 (142.1709 + 0.3817) | train = 145.7943 (145.3949 + 0.3994)
epoch 9: val = 138.8120 (138.5228 + 0.2892) | train = 141.1343 (140.8335 + 0.3008)
epoch 10: val = 133.9063 (133.6941 + 0.2122) | train = 136.6848 (136.4605 + 0.2243)
epoch 11: val = 130.2253 (130.0669 + 0.1585) | train = 131.9414 (131.7790 + 0.1624)
e

In [34]:
results_df_svae_svae.to_csv(base_path + "SVAE_SVAE_M1M2_results.csv")
results_df_svae_svae

Latent M1  Latent M2        Model  Accuracy       Std  N_test
0          5          5  svae + svae     0.802  0.013266     100
1          5         10  svae + svae     0.798  0.022271     100
2          5         50  svae + svae     0.876  0.016248     100
3         10          5  svae + svae     0.902  0.011662     100
4         10         10  svae + svae     0.910  0.010954     100
5         10         50  svae + svae     0.928  0.011662     100
6         50          5  svae + svae     0.932  0.007483     100
7         50         10  svae + svae     0.938  0.007483     100
8         50         50  svae + svae     0.942  0.004000     100

## **NVAE + NVAE**

In [35]:
results_df_nvae_nvae = launch_experiment("normal", "normal", test_loader)

Exploring latent1..:   0%|          | 0/3 [00:00<?, ?it/s]

Exploring latent2..:   0%|          | 0/3 [00:00<?, ?it/s]

Repeated runs..:   0%|          | 0/5 [00:00<?, ?it/s]


STARTING RUN n°1

[ + NVAE] Instantiating SVAE and optimizer..
[ + NVAE] Started training..

Moving Categorical Dist to cuda:0


Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

...

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 194.4773 (189.3060 + 5.1713) | train = 272.6645 (255.6839 + 16.9806)
epoch 2: val = 144.6167 (138.7578 + 5.8589) | train = 170.0812 (163.5042 + 6.5771)
epoch 3: val = 125.5245 (119.7087 + 5.8158) | train = 134.9227 (128.6649 + 6.2578)
epoch 4: val = 115.6770 (109.3918 + 6.2852) | train = 120.2919 (113.7992 + 6.4927)
epoch 5: val = 109.1524 (102.4839 + 6.6685) | train = 111.7305 (104.8500 + 6.8805)
epoch 6: val = 104.8197 (97.7515 + 7.0682) | train = 105.6054 (98.3126 + 7.2928)
epoch 7: val = 101.9183 (94.3976 + 7.5207) | train = 101.4479 (93.8633 + 7.5846)
epoch 8: val = 99.3844 (91.7396 + 7.6448) | train = 98.0606 (90.2269 + 7.8336)
epoch 9: val = 97.4923 (89.6217 + 7.8706) | train = 95.3470 (87.2974 + 8.0496)
epoch 10: val = 96.3869 (88.4314 + 7.9556) | train = 93.3252 (85.1541 + 8.1711)
epoch 11: val = 95.7266 (87.6961 + 8.0305) | train = 91.8683 (83.6146 + 8.2537)
epoch 12: val = 94.7

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 195.3593 (189.7502 + 5.6091) | train = 273.0155 (256.7237 + 16.2918)
epoch 2: val = 146.7664 (141.0632 + 5.7032) | train = 171.1366 (164.5747 + 6.5619)
epoch 3: val = 125.7834 (120.1453 + 5.6381) | train = 136.2482 (130.1565 + 6.0917)
epoch 4: val = 117.1894 (111.0078 + 6.1816) | train = 121.6534 (115.2776 + 6.3757)
epoch 5: val = 109.6081 (102.8216 + 6.7865) | train = 112.4560 (105.6659 + 6.7901)
epoch 6: val = 104.7626 (97.7310 + 7.0316) | train = 105.8102 (98.7047 + 7.1055)
epoch 7: val = 101.0015 (93.7339 + 7.2676) | train = 101.0815 (93.7391 + 7.3425)
epoch 8: val = 99.5966 (92.1766 + 7.4200) | train = 97.4862 (89.9490 + 7.5372)
epoch 9: val = 98.0319 (90.5230 + 7.5089) | train = 95.1748 (87.5248 + 7.6499)
epoch 10: val = 96.7084 (89.0672 + 7.6411) | train = 93.5400 (85.7887 + 7.7512)
epoch 11: val = 95.7726 (88.0283 + 7.7443) | train = 92.0050 (84.1460 + 7.8590)
epoch 12: val = 95.3

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 194.8170 (189.2343 + 5.5828) | train = 272.9375 (255.7554 + 17.1822)
epoch 2: val = 144.1830 (138.7199 + 5.4631) | train = 169.1216 (162.5259 + 6.5957)
epoch 3: val = 125.3886 (119.7244 + 5.6642) | train = 135.4019 (129.4075 + 5.9944)
epoch 4: val = 114.9638 (108.8694 + 6.0944) | train = 119.9857 (113.6855 + 6.3002)
epoch 5: val = 109.3737 (102.9735 + 6.4002) | train = 111.5157 (104.8782 + 6.6376)
epoch 6: val = 104.5923 (97.7296 + 6.8626) | train = 105.8271 (98.8229 + 7.0043)
epoch 7: val = 101.5341 (94.3190 + 7.2151) | train = 101.4219 (93.9975 + 7.4243)
epoch 8: val = 99.3534 (91.8525 + 7.5009) | train = 98.4418 (90.7253 + 7.7165)
epoch 9: val = 98.3932 (90.6306 + 7.7626) | train = 95.8590 (87.9447 + 7.9143)
epoch 10: val = 96.6426 (88.7917 + 7.8509) | train = 93.7711 (85.7192 + 8.0519)
epoch 11: val = 95.6787 (87.7409 + 7.9378) | train = 92.1906 (84.0395 + 8.1511)
epoch 12: val = 95.7

In [36]:
results_df_nvae_nvae.to_csv(base_path + "NVAE_NVAE_M1M2_results.csv")
results_df_nvae_nvae

Latent M1  Latent M2            Model  Accuracy       Std  N_test
0          5          5  normal + normal     0.840  0.037417     100
1          5         10  normal + normal     0.846  0.041761     100
2          5         50  normal + normal     0.824  0.024166     100
3         10          5  normal + normal     0.836  0.034986     100
4         10         10  normal + normal     0.842  0.035440     100
5         10         50  normal + normal     0.844  0.025768     100
6         50          5  normal + normal     0.750  0.053292     100
7         50         10  normal + normal     0.784  0.043635     100
8         50         50  normal + normal     0.788  0.019391     100

## **SVAE + NVAE**

In [37]:
results_df_svae_nvae = launch_experiment("svae", "normal", test_loader)

Exploring latent1..:   0%|          | 0/3 [00:00<?, ?it/s]

Exploring latent2..:   0%|          | 0/3 [00:00<?, ?it/s]

Repeated runs..:   0%|          | 0/5 [00:00<?, ?it/s]


STARTING RUN n°1

[SVAE + SVAE] Instantiating SVAE and optimizer..
[SVAE + SVAE] Started training..

Moving Categorical Dist to cuda:0


Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

...

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 220.2654 (218.3764 + 1.8890) | train = 376.9787 (373.2428 + 3.7360)
epoch 2: val = 206.5458 (204.5940 + 1.9518) | train = 212.4138 (210.4269 + 1.9869)
epoch 3: val = 198.2393 (196.3905 + 1.8488) | train = 202.7834 (200.8137 + 1.9697)
epoch 4: val = 192.4457 (190.7521 + 1.6936) | train = 195.4792 (193.6860 + 1.7931)
epoch 5: val = 174.6140 (173.2133 + 1.4006) | train = 185.1032 (183.4872 + 1.6159)
epoch 6: val = 157.4277 (156.3606 + 1.0671) | train = 165.1957 (163.9525 + 1.2432)
epoch 7: val = 149.2588 (148.3986 + 0.8602) | train = 153.7956 (152.8309 + 0.9647)
epoch 8: val = 143.7446 (143.0171 + 0.7275) | train = 146.8369 (146.0491 + 0.7879)
epoch 9: val = 137.5158 (136.8957 + 0.6200) | train = 140.8213 (140.1516 + 0.6697)
epoch 10: val = 133.5140 (132.9476 + 0.5664) | train = 135.3614 (134.7765 + 0.5849)
epoch 11: val = 130.3621 (129.8027 + 0.5594) | train = 131.4615 (130.9109 + 0.5506)
e

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 219.6555 (217.8209 + 1.8346) | train = 374.7771 (371.1362 + 3.6410)
epoch 2: val = 206.0267 (204.0711 + 1.9556) | train = 211.9724 (209.9896 + 1.9828)
epoch 3: val = 198.2613 (196.4185 + 1.8429) | train = 202.7658 (200.7945 + 1.9714)
epoch 4: val = 192.5104 (190.8146 + 1.6959) | train = 195.7445 (193.9492 + 1.7953)
epoch 5: val = 175.0663 (173.6318 + 1.4344) | train = 184.8283 (183.2124 + 1.6159)
epoch 6: val = 161.5564 (160.3939 + 1.1625) | train = 167.9564 (166.6557 + 1.3007)
epoch 7: val = 150.3342 (149.4263 + 0.9079) | train = 155.8834 (154.8600 + 1.0234)
epoch 8: val = 144.5534 (143.8133 + 0.7401) | train = 147.7143 (146.9122 + 0.8021)
epoch 9: val = 140.3469 (139.6919 + 0.6550) | train = 143.0065 (142.3279 + 0.6786)
epoch 10: val = 135.1092 (134.5330 + 0.5761) | train = 137.8761 (137.2633 + 0.6128)
epoch 11: val = 131.9961 (131.4343 + 0.5618) | train = 133.2281 (132.6617 + 0.5664)
e

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 220.8436 (218.9645 + 1.8791) | train = 379.4589 (375.8384 + 3.6205)
epoch 2: val = 205.3046 (203.3663 + 1.9383) | train = 211.7829 (209.7861 + 1.9968)
epoch 3: val = 196.9707 (195.1576 + 1.8131) | train = 201.5161 (199.5706 + 1.9455)
epoch 4: val = 187.2433 (185.5223 + 1.7210) | train = 193.8701 (192.0839 + 1.7862)
epoch 5: val = 166.1881 (164.8331 + 1.3549) | train = 177.0009 (175.4679 + 1.5330)
epoch 6: val = 154.2720 (153.2150 + 1.0570) | train = 160.5524 (159.3636 + 1.1887)
epoch 7: val = 146.6577 (145.8063 + 0.8514) | train = 150.4832 (149.5635 + 0.9197)
epoch 8: val = 140.5851 (139.8750 + 0.7101) | train = 143.7947 (143.0452 + 0.7495)
epoch 9: val = 137.6256 (136.9553 + 0.6702) | train = 138.7918 (138.1298 + 0.6621)
epoch 10: val = 131.6790 (131.0474 + 0.6317) | train = 134.1822 (133.5573 + 0.6249)
epoch 11: val = 127.9350 (127.3307 + 0.6044) | train = 129.4865 (128.9028 + 0.5837)
e

In [38]:
results_df_svae_nvae.to_csv(base_path + "SVAE_NVAE_M1M2_results.csv")
results_df_svae_nvae

Latent M1  Latent M2          Model  Accuracy       Std  N_test
0          5          5  svae + normal     0.816  0.016248     100
1          5         10  svae + normal     0.820  0.026077     100
2          5         50  svae + normal     0.818  0.011662     100
3         10          5  svae + normal     0.906  0.010198     100
4         10         10  svae + normal     0.904  0.010198     100
5         10         50  svae + normal     0.908  0.024819     100
6         50          5  svae + normal     0.932  0.007483     100
7         50         10  svae + normal     0.926  0.010198     100
8         50         50  svae + normal     0.938  0.007483     100

## **NVAE + SVAE**

In [39]:
results_df_nvae_svae = launch_experiment("normal", "svae", test_loader)

Exploring latent1..:   0%|          | 0/3 [00:00<?, ?it/s]

Exploring latent2..:   0%|          | 0/3 [00:00<?, ?it/s]

Repeated runs..:   0%|          | 0/5 [00:00<?, ?it/s]


STARTING RUN n°1

[ + NVAE] Instantiating SVAE and optimizer..
[ + NVAE] Started training..

Moving Categorical Dist to cuda:0


Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

...

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 192.2812 (184.6248 + 7.6564) | train = 271.8897 (252.9751 + 18.9146)
epoch 2: val = 145.7335 (139.2330 + 6.5004) | train = 168.3610 (160.5914 + 7.7696)
epoch 3: val = 126.3384 (120.7378 + 5.6005) | train = 135.7589 (129.8326 + 5.9264)
epoch 4: val = 115.9158 (110.1846 + 5.7312) | train = 120.5254 (114.7770 + 5.7484)
epoch 5: val = 109.5413 (103.9646 + 5.5767) | train = 111.5605 (105.8041 + 5.7564)
epoch 6: val = 105.0769 (99.5317 + 5.5452) | train = 105.9781 (100.3911 + 5.5870)
epoch 7: val = 102.1899 (96.5223 + 5.6676) | train = 101.6023 (95.9174 + 5.6849)
epoch 8: val = 99.6640 (93.8011 + 5.8629) | train = 98.2276 (92.3987 + 5.8289)
epoch 9: val = 97.8409 (91.8955 + 5.9454) | train = 95.6364 (89.6858 + 5.9506)
epoch 10: val = 96.1979 (90.1409 + 6.0570) | train = 93.7651 (87.6651 + 6.1001)
epoch 11: val = 95.9459 (89.6825 + 6.2634) | train = 92.2322 (86.0041 + 6.2282)
epoch 12: val = 95.

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 195.2978 (187.9830 + 7.3147) | train = 271.2586 (253.8993 + 17.3594)
epoch 2: val = 148.1286 (141.9549 + 6.1736) | train = 171.9683 (164.8722 + 7.0961)
epoch 3: val = 128.3950 (122.6857 + 5.7093) | train = 138.2387 (132.2780 + 5.9607)
epoch 4: val = 117.0088 (111.5016 + 5.5072) | train = 122.3810 (116.6839 + 5.6971)
epoch 5: val = 110.3337 (104.4450 + 5.8887) | train = 112.5846 (106.8162 + 5.7683)
epoch 6: val = 106.0438 (100.0998 + 5.9440) | train = 106.6572 (100.6408 + 6.0164)
epoch 7: val = 104.0271 (97.9214 + 6.1057) | train = 102.6467 (96.6060 + 6.0407)
epoch 8: val = 101.0858 (94.9668 + 6.1190) | train = 99.6795 (93.5337 + 6.1458)
epoch 9: val = 99.2893 (93.2395 + 6.0499) | train = 97.2806 (91.0832 + 6.1975)
epoch 10: val = 97.4917 (91.3682 + 6.1234) | train = 94.7098 (88.5288 + 6.1810)
epoch 11: val = 96.8125 (90.6342 + 6.1783) | train = 92.9625 (86.7325 + 6.2301)
epoch 12: val = 9

Epochs..:   0%|          | 0/500 [00:00<?, ?it/s]

Loss printing format:
epoch x: val = M1 loss + M2 loss | train = M1 loss + M2 loss

epoch 1: val = 196.3503 (189.2587 + 7.0916) | train = 274.1320 (256.4466 + 17.6855)
epoch 2: val = 146.7189 (140.1403 + 6.5786) | train = 171.4856 (164.1678 + 7.3179)
epoch 3: val = 126.9300 (121.3540 + 5.5760) | train = 135.5897 (129.8075 + 5.7822)
epoch 4: val = 115.9667 (110.4419 + 5.5248) | train = 120.7781 (115.1733 + 5.6048)
epoch 5: val = 109.6793 (104.0825 + 5.5968) | train = 111.9755 (106.2994 + 5.6761)
epoch 6: val = 105.5394 (99.6611 + 5.8783) | train = 106.1967 (100.3271 + 5.8696)
epoch 7: val = 102.7101 (96.5774 + 6.1327) | train = 102.2504 (96.2466 + 6.0037)
epoch 8: val = 100.3654 (94.1285 + 6.2369) | train = 98.9455 (92.8036 + 6.1419)
epoch 9: val = 98.6620 (92.5521 + 6.1099) | train = 96.3375 (90.1712 + 6.1663)
epoch 10: val = 97.2103 (91.0940 + 6.1163) | train = 94.1947 (88.0718 + 6.1229)
epoch 11: val = 96.2176 (90.1860 + 6.0316) | train = 92.6694 (86.5853 + 6.0841)
epoch 12: val = 95

In [40]:
results_df_nvae_svae.to_csv(base_path + "NVAE_SVAE_M1M2_results.csv")
results_df_nvae_svae

Latent M1  Latent M2          Model  Accuracy       Std  N_test
0          5          5  normal + svae     0.834  0.020591     100
1          5         10  normal + svae     0.814  0.031369     100
2          5         50  normal + svae     0.848  0.024819     100
3         10          5  normal + svae     0.796  0.037202     100
4         10         10  normal + svae     0.808  0.030594     100
5         10         50  normal + svae     0.846  0.037736     100
6         50          5  normal + svae     0.696  0.047582     100
7         50         10  normal + svae     0.686  0.017436     100
8         50         50  normal + svae     0.694  0.033226     100